In [11]:
import pandas as pd
import numpy as np

import folium
from folium.plugins import AntPath

from pprint import pprint
from pprint import PrettyPrinter

In [12]:
df_intercambio = pd.read_csv('../Obtencion datos/intercambio_electrico.csv')

df_intercambio = df_intercambio.drop(columns=['Unnamed: 0'])

df_intercambio

nombre tipo de intercambio  Valores  Porcentaje Fecha actualización
0      Francia         Exportación  -2873.3    0.040691          01/01/2022
1      Francia         Exportación  -2674.3    0.033530          02/01/2022
2      Francia         Exportación  -6444.3    0.078966          03/01/2022
3      Francia         Exportación -41761.7    0.727676          04/01/2022
4      Francia         Exportación -42497.1    0.801499          05/01/2022
...        ...                 ...      ...         ...                 ...
10531  Andorra               Saldo    -24.0    1.000000          11/10/2024
10532  Andorra               Saldo   -159.0    1.000000          12/10/2024
10533  Andorra               Saldo   -369.0    1.000000          13/10/2024
10534  Andorra               Saldo    -68.0    1.000000          14/10/2024
10535  Andorra               Saldo   -122.0    1.000000          15/10/2024

[10536 rows x 5 columns]

In [13]:
df_intercambio.columns

Index(['nombre', 'tipo de intercambio', 'Valores', 'Porcentaje',
       'Fecha actualización'],
      dtype='object')

In [14]:
df_intercambio['nombre'].unique()

array(['Francia', 'Portugal', 'Marruecos', 'Andorra'], dtype=object)

In [15]:
df_intercambio['tipo de intercambio'].unique()

array(['Exportación', 'Importación', 'Saldo'], dtype=object)

In [16]:
def mapa_intercambio_energ(df):
  #Creamos mapa base:
  españa_alt = 40.4637
  españa_lat = -3.7492

  #Creacion del mapa

  from IPython.display import display

  spain_map = folium.Map(location = [españa_alt, españa_lat],
                       zoom_start= 5,
                       tiles = 'Esri Worldimagery',
                       width='500px',
                       height='500px'
                       )

  bounds =   [[51.1242, -17.0000],[20.0000, 9.6625]]

  spain_map.fit_bounds(bounds)


  #Coordenadas de los paises donde existe un intercambio energetico.
  lista_paises = ['Marruecos', 'Francia', 'Portugal', 'Andorra', 'España']
  lista_altitudes = [31.83999, 46.57771, 39.68023, 42.5462, 40.4637]
  lista_latitudes = [-6.19721, 2.78159, -8.80606, 1.5034, -3.7492]

  df_coordenadas = pd.DataFrame()
  df_coordenadas['nombre'] = lista_paises
  df_coordenadas['altitud'] = lista_altitudes
  df_coordenadas['latitud'] = lista_latitudes


  #Creacion de variables con sus coordenadas
  marruecos = [df_coordenadas['altitud'][0], df_coordenadas['latitud'][0]]
  francia = [df_coordenadas['altitud'][1], df_coordenadas['latitud'][1]]
  portugal = [df_coordenadas['altitud'][2], df_coordenadas['latitud'][2]]
  andorra = [df_coordenadas['altitud'][3], df_coordenadas['latitud'][3]]
  españa = [df_coordenadas['altitud'][4], df_coordenadas['latitud'][4]]


  #Unión de df_coordenadas y df incluido en la función - en nuestro caso, df_intercambio.
  df_unido = pd.merge(df_intercambio, df_coordenadas, how = 'left', on = 'nombre')

  #Creación de iconos por país
  españa_url = "https://upload.wikimedia.org/wikipedia/en/9/9a/Flag_of_Spain.svg"
  españa_icon = folium.CustomIcon(españa_url, icon_size=(50, 30))

  marruecos_url = "https://upload.wikimedia.org/wikipedia/commons/2/2c/Flag_of_Morocco.svg"
  marruecos_icon = folium.CustomIcon(marruecos_url, icon_size=(40, 20))

  andorra_url = "https://upload.wikimedia.org/wikipedia/commons/1/19/Flag_of_Andorra.svg"
  andorra_icon = folium.CustomIcon(andorra_url, icon_size=(40, 20))

  francia_url = "https://upload.wikimedia.org/wikipedia/en/c/c3/Flag_of_France.svg"
  francia_icon = folium.CustomIcon(francia_url, icon_size=(40, 20))

  portugal_url = "https://upload.wikimedia.org/wikipedia/commons/5/5c/Flag_of_Portugal.svg"
  portugal_icon = folium.CustomIcon(portugal_url, icon_size=(40, 20))


#CREACIÓN DEL MAPA CON INFORMACIÓN
  intercambios = folium.map.FeatureGroup(name='Intercambios')
  ##IMPUT DEL TIPO DE INFORMACIÓN DESEADA.
  input_tipo_inter = input('Introduce el tipo de intercambio: importación, exportación, o saldo: ______ ').lower()
  ## df_filtrado es el df resultante del tipo de intercambio deseado.
  df_filtrado = df_unido[df_unido['tipo de intercambio'].str.lower() == input_tipo_inter]


  for lat, lng, pais, valores, porcentaje, fecha in zip(df_filtrado['altitud'],
                           df_filtrado['latitud'],
                           df_filtrado['nombre'],
                           df_filtrado['Valores'],
                           df_filtrado['Porcentaje'],
                           df_filtrado['Fecha actualización']):

        contenido_label = f'''<b> Pais: {pais} </b><br>
                            <b>Tipo de intercambio: {input_tipo_inter} </b><br>
                            <b>Valores: {valores} </b><br>
                            <b>Porcentaje: {porcentaje} </b><br>
                            <b>Fecha actualización: {fecha} </b>'''
        intercambios.add_child(folium.Marker(location=[lat, lng],
                                        popup=contenido_label))



  spain_map.add_child(intercambios)





  folium.Marker(
          location= españa,
          icon=españa_icon,
          popup = 'España'
          ).add_to(spain_map)

  folium.Marker(
          location= portugal,
          icon=portugal_icon,
          popup = 'Portugal'
          ).add_to(spain_map)
  folium.Marker(
          location= francia,
          icon=francia_icon,
          popup = 'Francia'
          ).add_to(spain_map)
  folium.Marker(
          location= marruecos,
          icon=marruecos_icon,
          popup = 'Marruecos'
          ).add_to(spain_map)
  folium.Marker(
          location= andorra,
          icon=andorra_icon,
          popup = 'Andorra'
          ).add_to(spain_map)




  for i, v in df_filtrado[df_filtrado['nombre'] == 'Francia'].iterrows():
        if v['Valores'] < 0:
                AntPath(locations = [españa, francia],
                color = 'blue',
                delay = 2000,
                weight = 5).add_to(spain_map)
        elif v['Valores'] > 0:
                AntPath(locations = [francia,españa],
                color = 'blue',
                delay = 2000,
                weight = 5).add_to(spain_map)
        else:
                pass

  for i, v in df_filtrado[df_filtrado['nombre'] == 'Andorra'].iterrows():
        if v['Valores'] < 0:
                AntPath(locations = [españa, andorra],
                color = 'orange',
                delay = 2000,
                weight = 5).add_to(spain_map)
        elif v['Valores'] > 0:
                AntPath(locations = [andorra,españa],
                color = 'orange',
                delay = 2000,
                weight = 5).add_to(spain_map)
        else:
                pass

  for i, v in df_filtrado[df_filtrado['nombre'] == 'Marruecos'].iterrows():
        if v['Valores'] < 0:
                AntPath(locations = [españa, marruecos],
                color = 'red',
                delay = 2000,
                weight = 5).add_to(spain_map)
        elif v['Valores'] > 0:
                AntPath(locations = [marruecos, españa],
                color = 'red',
                delay = 2000,
                weight = 5).add_to(spain_map)
        else:
                pass

  for i, v in df_filtrado[df_filtrado['nombre'] == 'Portugal'].iterrows():
        if v['Valores'] < 0:
                AntPath(locations = [españa, portugal],
                color = 'green',
                delay = 2000,
                weight = 5).add_to(spain_map)
        elif v['Valores'] > 0:
                AntPath(locations = [portugal, españa],
                color = 'green',
                delay = 2000,
                weight = 5).add_to(spain_map)
        else:
                pass



        return spain_map









In [17]:
mapa_intercambio_energ(df_intercambio)